***AVISO**: Esse Notebook foi feito com base na estrutura do Databricks Free Edition, que utiliza catálogos.*

# **ETAPA 3 - PROCESSAMENTO PARA CAMADA SILVER**

---
---

<br>

Essa etapa será responsável por mover os dados para a camada silver, limpando e filtrandoos dados.

*`Complete as informações necessárias nos trechos que estão destacados em vermelho assim como esse, seguindo o padrão snake_case.`*

<br><br>

---
---

### Parte 1 - **Importação das Bibliotecas Necessárias**

In [0]:
import gc
from pyspark.sql import SparkSession
from pyspark.sql.functions import *
from pyspark.sql.types import *
from pyspark.sql.window import Window

### Parte 2 - **Otimizar a Sessão com configurações Personalizadas**

Aqui o será configurado algumas propriedades para que o desempenho da sessão seja mais otimizado 
- Define tamanho fixo de partições para o shuffle para melhorar o paralelismo (usar ***número de partições = número de núclos de CPU * 2 ou 3*** para encontrar melhor cenário possível)
- Define o tamanho máximo de partições para evitar muitos arquivos pequenos
- Usa o codec Snappy para compressão rápida, otimizando tempo de leitura e escrita
- Habilita otimizações adaptativas, ajustando o número de partições dinamicamente com base no tamanho dos dados
- Habilita a escrita otimizada para tabelas Delta Lake, reduzindo a criação de pequenos arquivos durante operações de escrita
- Ativa a compactação automática de arquivos Delta, melhorando a performance de leitura e manutenção das tabelas

In [0]:
spark = (
    SparkSession.builder
        .appName("Silver Layer - Transformations")
        .config("spark.sql.shuffle.partitions", "200")
        .config("spark.sql.files.maxPartitionBytes", "134217728") 
        .config("spark.sql.parquet.compression.codec", "snappy")
        .config("spark.sql.adaptive.enabled", "true")
        .config("spark.databricks.delta.optimizeWrite.enabled", "true")
        .config("spark.databricks.delta.autoCompact.enabled", "true")
        .getOrCreate()
)

### Parte 3 - **Definindo Origens, Arquivos e Destinos**

`Insira nas variáveis:` <br>
- `nome_datalakehouse --> nome do Data Lakehouse `
- `nome_camada_bronze --> nome da camada de origem dos dados`
- `nome_volume_bronze --> nome do volume de origem dos dados dentro da camada`
- `nome_camada_silver --> nome da camada de destino dos dados`
- `nome_volume_silver --> nome do volume de destino dos dados dentro da camada`

In [0]:
nome_datalakehouse = "dataexperts"

nome_camada_bronze = "bronze"
nome_volume_bronze = "vendas_atual" 

nome_camada_silver = "silver"
nome_volume_silver = "vendas" 

O código a seguir armazena em variáveis os caminhos já prontos de origem e de destino dos dados:

In [0]:
origem_dados = f"/Volumes/{nome_datalakehouse}/{nome_camada_bronze}/{nome_volume_bronze}"
destino_dados = f"/Volumes/{nome_datalakehouse}/{nome_camada_silver}/{nome_volume_silver}"

O código a seguir cria o volume de destino caso ele ainda não exista:

In [0]:
spark.sql(f"CREATE VOLUME IF NOT EXISTS {nome_datalakehouse}.{nome_camada_silver}.{nome_volume_silver}")

DataFrame[]

`Insira no vetor todos os arquivos que deseja fazer esse processamento para camada silver:` <br>

In [0]:
bronze_tables = {
    "dim_categoria": "bronze_dim_categoria_produto",
    "dim_cliente": "bronze_dim_cliente",        
    "dim_data": "bronze_dim_data",
    "dim_localidade": "bronze_dim_localidade",                
    "dim_produto": "bronze_dim_produto",                    
    "fato_vendas": "bronze_fato_vendas"                                 
}

bronze_dfs = {                            
    nome: spark.read.format("delta").load(f"{origem_dados}/{tabela}")
    for nome, tabela in bronze_tables.items()
}

### Parte 4 - **Limpando e Filtrando os Dados**

A seguir código para substituir os valores null por N/A:

In [0]:
def replace_null_string(df):
    for coluna, tipo in df.dtypes:
        if tipo == "string" and not coluna.endswith("_id"):
            df = df.withColumn(                                            
                coluna,
                when(col(coluna).isNull(), lit("N/A")).otherwise(col(coluna))
            )
    return df

A seguir código para adicionar SK's:

In [0]:
def add_surrogate_key(df, sk_name):
    window = Window.orderBy(lit(1))
    return df.withColumn(sk_name, row_number().over(window).cast("long"))

Função para traduzir "0" para "False" e "1" para "True":

In [0]:
def byte_to_bool(df):
    df = df.withColumn(
        "final_de_semana",
        when(col("final_de_semana") == 0, lit(False))
        .otherwise(lit(True))
    )
    return df

Função para escrever os nomes dos meses em extenso

In [0]:
def mes_nome(df):
    df = df.withColumn(
        "mes",
        when(col("mes") == 1, lit("Janeiro"))
        .when(col("mes") == 2, lit("Fevereiro"))
        .when(col("mes") == 3, lit("Março"))
        .when(col("mes") == 4, lit("Abril"))
        .when(col("mes") == 5, lit("Maio"))
        .when(col("mes") == 6, lit("Junho"))
        .when(col("mes") == 7, lit("Julho"))
        .when(col("mes") == 8, lit("Agosto"))
        .when(col("mes") == 9, lit("Setembro"))
        .when(col("mes") == 10, lit("Outubro"))
        .when(col("mes") == 11, lit("Novembro"))
        .otherwise(lit("Dezembro"))
    )
    return df

A seguir código para transformar as dimensões:

In [0]:
# Dimensão Categoria
silver_dim_categoria = (
    bronze_dfs["dim_categoria"]
        .dropDuplicates(["categoria_id"])
        .withColumn("categoria_nome", upper(trim(col("categoria_nome"))))
)
silver_dim_categoria = replace_null_string(silver_dim_categoria)
silver_dim_categoria = add_surrogate_key(silver_dim_categoria, "sk_categoria")

# Dimensão Cliente
silver_dim_cliente = (
    bronze_dfs["dim_cliente"]
        .dropDuplicates(["cliente_id"])
        .withColumn("nome_cliente", initcap(trim(col("nome_cliente"))))
        .withColumn("estado_cliente", upper(col("estado"))) 
        .withColumn("cidade_cliente", initcap(col("cidade"))) 
        .drop("estado", "cidade")
)
silver_dim_cliente = replace_null_string(silver_dim_cliente)
silver_dim_cliente = add_surrogate_key(silver_dim_cliente, "sk_cliente")

# Dimensão Data
silver_dim_data = (
    bronze_dfs["dim_data"]
        .dropDuplicates(["data_id"])
)
silver_dim_data = byte_to_bool(silver_dim_data)
silver_dim_data = mes_nome(silver_dim_data)
silver_dim_data = replace_null_string(silver_dim_data)
silver_dim_data = add_surrogate_key(silver_dim_data, "sk_data")

# Dimensão Localidade
silver_dim_localidade = (
    bronze_dfs["dim_localidade"]
        .dropDuplicates(["localidade_id"])
        .withColumn("estado_venda", upper(col("estado"))) # renomear coluna
        .withColumn("cidade_venda", initcap(col("cidade"))) # renomear coluna
        .drop("estado", "cidade")
)
silver_dim_localidade = replace_null_string(silver_dim_localidade)
silver_dim_localidade = add_surrogate_key(silver_dim_localidade, "sk_localidade")

# Dimensão Produto
silver_dim_produto = (
    bronze_dfs["dim_produto"]
        .dropDuplicates(["produto_id"])
        .drop("categoria_nome") # remover categoria_nome
        # .withColumn("categoria_nome", upper(col("categoria_nome")))
)
silver_dim_produto = replace_null_string(silver_dim_produto)
silver_dim_produto = add_surrogate_key(silver_dim_produto, "sk_produto")

/databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/expressions.py:1134: UserWarning: WARN WindowExpression: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
  warnings.warn(


A seguir código para transformar o fato:

In [0]:
silver_fato_vendas = (
    bronze_dfs["fato_vendas"]
        .dropDuplicates(["venda_id"])
        .filter(col("quantidade") > 0)
        # Categoria
        .join(
            silver_dim_categoria.select("categoria_id", "sk_categoria"),
            on="categoria_id",
            how="left"
        )
        # Cliente
        .join(
            silver_dim_cliente.select("cliente_id", "sk_cliente"),
            on="cliente_id",
            how="left"
        )
        # Produto
        .join(
            silver_dim_produto.select("produto_id", "sk_produto"),
            on="produto_id",
            how="left"
        )
        # Data
        .join(
            silver_dim_data.select("data_id", "sk_data"),
            on="data_id",
            how="left"
        )
        # Localidade
        .join(
            silver_dim_localidade.select("localidade_id", "sk_localidade"),
            on="localidade_id",
            how="left"
        )
)
# Removendo FKs null
silver_fato_vendas = silver_fato_vendas.filter(
    col("sk_categoria").isNotNull() & 
    col("sk_cliente").isNotNull() &
    col("sk_produto").isNotNull() &
    col("sk_data").isNotNull() &
    col("sk_localidade").isNotNull()
)
# Removendo id's
silver_fato_vendas = silver_fato_vendas.drop(
    "categoria_id",
    "cliente_id",
    "produto_id",
    "data_id",
    "localidade_id"
)

/databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/expressions.py:1134: UserWarning: WARN WindowExpression: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
  warnings.warn(


### Parte 5 - **Salvando na Camada Silver**

A seguir, código que salva todas as modificações e os novos arquivos na camada silver:

In [0]:
silver_tables = {
    "silver_dim_categoria_produto": silver_dim_categoria,
    "silver_dim_cliente": silver_dim_cliente,
    "silver_dim_data": silver_dim_data,
    "silver_dim_localidade": silver_dim_localidade,
    "silver_dim_produto": silver_dim_produto,
    "silver_fato_vendas": silver_fato_vendas
}

for nome_tabela, df in silver_tables.items():
    (
        df.write
        .format("delta")
        .mode("overwrite")
        .save(f"{destino_dados}/{nome_tabela}")
    )

/databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/expressions.py:1134: UserWarning: WARN WindowExpression: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
  warnings.warn(


### Parte 6 - **Limpeza de Cache e Outros**

O código a seguir libera memória de objetos não mais utilizados:

In [0]:
del bronze_dfs
del silver_tables

gc.collect()

29514


<br>

---
---

### **Resultados**

Aqui é um log simples para mostrar se deu certo ou não toda a construção da arquitetura planejada.

In [0]:
# %skip
silver_dim_categoria_produto = spark.read.format("delta").load("/Volumes/dataexperts/silver/vendas/silver_dim_categoria_produto")
display(silver_dim_categoria_produto)

silver_dim_cliente = spark.read.format("delta").load("/Volumes/dataexperts/silver/vendas/silver_dim_cliente")
display(silver_dim_cliente)

silver_dim_data = spark.read.format("delta").load("/Volumes/dataexperts/silver/vendas/silver_dim_data")
display(silver_dim_data)

silver_dim_localidade = spark.read.format("delta").load("/Volumes/dataexperts/silver/vendas/silver_dim_localidade")
display(silver_dim_localidade)

silver_dim_produto = spark.read.format("delta").load("/Volumes/dataexperts/silver/vendas/silver_dim_produto")
display(silver_dim_produto)

silver_fato_vendas = spark.read.format("delta").load("/Volumes/dataexperts/silver/vendas/silver_fato_vendas")
display(silver_fato_vendas)

categoria_id categoria_nome _source_file _ingestion_date sk_categoria 8 ESPORTES categoria_produto_20260206_022705.csv 2026-02-06T05:27:19.031Z 1 11 PAPELARIA categoria_produto_20260206_022705.csv 2026-02-06T05:27:19.031Z 2 2 ELETRODOMÉSTICOS categoria_produto_20260206_022705.csv 2026-02-06T05:27:19.031Z 3 12 PET SHOP categoria_produto_20260206_022705.csv 2026-02-06T05:27:19.031Z 4 1 ELETRÔNICOS categoria_produto_20260206_022705.csv 2026-02-06T05:27:19.031Z 5 10 BRINQUEDOS categoria_produto_20260206_022705.csv 2026-02-06T05:27:19.031Z 6 7 COSMÉTICOS categoria_produto_20260206_022705.csv 2026-02-06T05:27:19.031Z 7 3 ALIMENTOS categoria_produto_20260206_022705.csv 2026-02-06T05:27:19.031Z 8 5 VESTUÁRIO categoria_produto_20260206_022705.csv 2026-02-06T05:27:19.031Z 9 4 BEBIDAS categoria_produto_20260206_022705.csv 2026-02-06T05:27:19.031Z 10 6 CALÇADOS categoria_produto_20260206_022705.csv 2026-02-06T05:27:19.031Z 11 9 MÓVEIS categoria_produto_20260206_022705.csv 2026-02-06T05:27:19.031Z 12

cliente_id nome_cliente _source_file _ingestion_date estado_cliente cidade_cliente sk_cliente 271 Cliente 0271 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z AL Maceió 1 372 Cliente 0372 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z TO Palmas 2 722 Cliente 0722 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z CE Juazeiro Do Norte 3 212 Cliente 0212 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z ES Vila Velha 4 234 Cliente 0234 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z BA Feira De Santana 5 362 Cliente 0362 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z SP Sorocaba 6 331 Cliente 0331 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z PE Jaboatão Dos Guararapes 7 547 Cliente 0547 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z SC Florianópolis 8 459 Cliente 0459 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z PA Santarém 9 673 Cliente 0673 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z CE Maracanaú 10 290 Cliente 0290 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z RO Porto Velho 11 823 Cliente 0823 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z CE Caucaia 12 332 Cliente 0332 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z PA Ananindeua 13 435 Cliente 0435 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z BA Feira De Santana 14 240 Cliente 0240 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z MG Juiz De Fora 15 117 Cliente 0117 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z AM Itacoatiara 16 184 Cliente 0184 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z PR Maringá 17 382 Cliente 0382 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z MG Uberlândia 18 854 Cliente 0854 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z SP Osasco 19 873 Cliente 0873 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z PR Curitiba 20 203 Cliente 0203 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z SP São José Dos Campos 21 914 Cliente 0914 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z AM Itacoatiara 22 703 Cliente 0703 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z AP Macapá 23 762 Cliente 0762 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z SP Campinas 24 779 Cliente 0779 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z RN Natal 25 62 Cliente 0062 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z MG Betim 26 477 Cliente 0477 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z MG Belo Horizonte 27 512 Cliente 0512 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z MG Betim 28 880 Cliente 0880 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z RS Santa Maria 29 263 Cliente 0263 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z MG Juiz De Fora 30 305 Cliente 0305 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z PE Jaboatão Dos Guararapes 31 667 Cliente 0667 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z MG Belo Horizonte 32 851 Cliente 0851 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z PR Cascavel 33 247 Cliente 0247 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z MG Contagem 34 651 Cliente 0651 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z RJ Rio De Janeiro 35 700 Cliente 0700 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z PE Jaboatão Dos Guararapes 36 8 Cliente 0008 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z DF Brasília 37 706 Cliente 0706 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z PR Curitiba 38 875 Cliente 0875 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z RN Mossoró 39 896 Cliente 0896 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z MG Contagem 40 596 Cliente 0596 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z MA Imperatriz 41 831 Cliente 0831 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z CE Juazeiro Do Norte 42 498 Cliente 0498 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z TO Palmas 43 434 Cliente 0434 cliente_20260206_022706.csv 2026-02-06T05:27:21.170Z SP Ribeirão Preto 44 867 Cliente 0867 cliente_20260206_022706.csv 2026-02

data_id data ano mes dia dia_semana final_de_semana _source_file _ingestion_date sk_data 20220602 2022-06-02 2022 Junho 2 quinta false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 1 20230818 2023-08-18 2023 Agosto 18 sexta false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 2 20251006 2025-10-06 2025 Outubro 6 segunda false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 3 20240410 2024-04-10 2024 Abril 10 quarta false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 4 20241001 2024-10-01 2024 Outubro 1 terça false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 5 20220717 2022-07-17 2022 Julho 17 domingo true data_20260206_022706.csv 2026-02-06T05:27:23.256Z 6 20230902 2023-09-02 2023 Setembro 2 sábado true data_20260206_022706.csv 2026-02-06T05:27:23.256Z 7 20250310 2025-03-10 2025 Março 10 segunda false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 8 20250626 2025-06-26 2025 Junho 26 quinta false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 9 20240403 2024-04-03 2024 Abril 3 quarta false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 10 20240727 2024-07-27 2024 Julho 27 sábado true data_20260206_022706.csv 2026-02-06T05:27:23.256Z 11 20231025 2023-10-25 2023 Outubro 25 quarta false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 12 20220303 2022-03-03 2022 Março 3 quinta false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 13 20220311 2022-03-11 2022 Março 11 sexta false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 14 20240506 2024-05-06 2024 Maio 6 segunda false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 15 20230809 2023-08-09 2023 Agosto 9 quarta false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 16 20221004 2022-10-04 2022 Outubro 4 terça false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 17 20240303 2024-03-03 2024 Março 3 domingo true data_20260206_022706.csv 2026-02-06T05:27:23.256Z 18 20250520 2025-05-20 2025 Maio 20 terça false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 19 20221202 2022-12-02 2022 Dezembro 2 sexta false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 20 20230424 2023-04-24 2023 Abril 24 segunda false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 21 20221001 2022-10-01 2022 Outubro 1 sábado true data_20260206_022706.csv 2026-02-06T05:27:23.256Z 22 20230312 2023-03-12 2023 Março 12 domingo true data_20260206_022706.csv 2026-02-06T05:27:23.256Z 23 20240105 2024-01-05 2024 Janeiro 5 sexta false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 24 20240412 2024-04-12 2024 Abril 12 sexta false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 25 20250404 2025-04-04 2025 Abril 4 sexta false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 26 20230630 2023-06-30 2023 Junho 30 sexta false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 27 20220404 2022-04-04 2022 Abril 4 segunda false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 28 20241028 2024-10-28 2024 Outubro 28 segunda false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 29 20250427 2025-04-27 2025 Abril 27 domingo true data_20260206_022706.csv 2026-02-06T05:27:23.256Z 30 20250423 2025-04-23 2025 Abril 23 quarta false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 31 20250616 2025-06-16 2025 Junho 16 segunda false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 32 20250728 2025-07-28 2025 Julho 28 segunda false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 33 20221020 2022-10-20 2022 Outubro 20 quinta false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 34 20240309 2024-03-09 2024 Março 9 sábado true data_20260206_022706.csv 2026-02-06T05:27:23.256Z 35 20250628 2025-06-28 2025 Junho 28 sábado true data_20260206_022706.csv 2026-02-06T05:27:23.256Z 36 20230119 2023-01-19 2023 Janeiro 19 quinta false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 37 20250827 2025-08-27 2025 Agosto 27 quarta false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 38 20221227 2022-12-27 2022 Dezembro 27 terça false data_20260206_022706.csv 2026-02-06T05:27:23.256Z 39 20250507 2025-05

localidade_id _source_file _ingestion_date estado_venda cidade_venda sk_localidade 62 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z RO Porto Velho 1 8 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z BA Ilhéus 2 38 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z PB Campina Grande 3 39 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z PB João Pessoa 4 49 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z PR Londrina 5 26 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z MG Betim 6 33 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z MT Cuiabá 7 40 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z PE Caruaru 8 11 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z BA Vitória Da Conquista 9 71 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z SC Chapecó 10 35 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z PA Ananindeua 11 46 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z PR Cascavel 12 20 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z GO Anápolis 13 87 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z TO Palmas 14 2 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z AL Maceió 15 12 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z CE Caucaia 16 43 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z PE Recife 17 31 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z MS Campo Grande 18 1 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z AL Arapiraca 19 41 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z PE Jaboatão Dos Guararapes 20 44 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z PI Parnaíba 21 68 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z RS Porto Alegre 22 58 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z RJ Volta Redonda 23 54 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z RJ Niterói 24 55 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z RJ Nova Iguaçu 25 45 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z PI Teresina 26 85 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z SP São José Dos Campos 27 63 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z RR Boa Vista 28 27 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z MG Contagem 29 74 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z SC Itajaí 30 82 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z SP Ribeirão Preto 31 75 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z SC Joinville 32 50 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z PR Maringá 33 10 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z BA Salvador 34 16 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z DF Brasília 35 7 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z BA Feira De Santana 36 53 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z RJ Duque De Caxias 37 19 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z ES Vitória 38 79 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z SP Diadema 39 21 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z GO Aparecida De Goiânia 40 76 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z SP Barueri 41 3 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z AM Itacoatiara 42 5 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z AP Macapá 43 14 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z CE Juazeiro Do Norte 44 23 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z MA Imperatriz 45 81 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z SP Osasco 46 77 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z SP Campinas 47 18 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z ES Vila Velha 48 60 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z RN Natal 49 83 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z SP Santos 50 51 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z PR Ponta Grossa 51 59 localidade_20260206_022706.csv 2026-02-06T05:27:25.121Z RN Moss

produto_id preco_lista _source_file _ingestion_date sk_produto 271 64.38 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 1 212 53.59 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 2 234 18.34 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 3 290 18.66 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 4 240 45.22 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 5 117 26.55 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 6 184 36.22 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 7 203 51.93 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 8 62 24.25 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 9 263 5.0 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 10 247 20.39 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 11 8 42.97 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 12 38 8.37 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 13 39 12.22 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 14 49 33.32 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 15 159 13.27 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 16 170 17.25 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 17 192 45.32 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 18 193 30.83 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 19 26 28.98 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 20 96 11.27 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 21 33 26.89 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 22 40 30.51 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 23 141 31.08 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 24 288 38.59 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 25 11 20.53 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 26 287 24.75 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 27 125 38.56 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 28 187 36.02 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 29 94 22.27 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 30 71 33.68 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 31 35 44.41 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 32 214 40.08 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 33 46 17.6 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 34 20 11.62 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 35 255 10.9 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 36 185 23.71 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 37 111 8.57 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 38 87 46.96 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 39 2 24.95 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 40 12 20.5 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 41 210 273.59 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 42 43 25.3 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 43 297 46.51 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 44 31 18.9 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 45 1 36.53 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 46 41 42.23 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 47 208 36.9 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 48 135 15.62 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 49 250 34.57 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 50 44 22.63 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 51 256 20.28 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 52 139 44.17 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 53 173 25.89 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 54 166 34.73 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 55 224 10.3 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 56 298 32.6 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 57 207 36.93 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 58 278 18.91 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 59 265 23.3 produto_20260206_022707.csv 2026-02-06T05:27:27.044Z 60 100 23.55 produto_202602

venda_id quantidade preco_lista valor_total _source_file _ingestion_date sk_categoria sk_cliente sk_produto sk_data sk_localidade 271 2 83.72 167.44 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 10 296 260 695 55 1785 1 40.02 40.02 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 8 402 101 683 46 1898 2 13.22 26.44 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 3 598 162 449 24 2851 1 40.43 40.43 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 6 56 138 382 60 7312 2 48.49 96.98 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 11 4 208 1432 80 7347 1 22.83 22.83 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 5 182 117 466 5 9762 2 43.6 87.2 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 12 640 285 617 18 10523 2 21.69 43.38 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 6 220 174 856 37 10696 1 22.14 22.14 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 3 535 150 946 19 14640 1 44.21 44.21 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 12 252 285 534 20 15392 2 21.16 42.32 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 12 991 247 706 46 15961 1 18.74 18.74 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 1 367 251 1306 20 16211 1 22.25 22.25 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 11 424 72 1 51 17620 2 12.63 25.26 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 4 545 289 1141 20 18741 1 30.05 30.05 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 4 91 245 399 10 21117 4 24.16 96.64 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 6 998 265 287 9 21549 2 7.64 15.28 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 5 212 221 55 84 23069 1 27.61 27.61 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 4 120 6 937 41 23798 1 42.94 42.94 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 6 60 132 918 33 24338 5 15.97 79.85 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 5 149 146 682 52 28141 2 39.71 79.42 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 4 403 79 1417 29 28793 2 11.85 23.7 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 5 65 262 1280 87 29079 1 15.17 15.17 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 10 141 74 691 50 31266 3 43.89 131.67 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 5 876 12 1105 8 31384 1 37.18 37.18 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 3 768 236 260 32 31400 3 39.81 119.43 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 10 179 100 130 6 32087 1 41.06 41.06 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 5 881 39 1028 67 36103 2 28.44 56.88 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 12 922 201 416 85 37666 2 21.25 42.5 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 9 125 249 433 25 41730 1 40.06 40.06 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 3 623 44 906 57 42923 2 51.24 102.48 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 12 865 8 629 67 43866 1 26.28 26.28 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 12 131 153 624 31 44440 1 26.26 26.26 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 7 854 82 474 34 44649 2 46.88 93.76 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 5 546 297 964 13 45544 1 44.33 44.33 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 5 140 39 1 38 45782 2 32.31 64.62 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 1 865 283 454 39 47545 1 14.92 14.92 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 4 281 286 90 21 48880 3 39.36 118.08 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 10 704 217 698 31 49292 1 13.29 13.29 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 9 822 104 1253 77 49964 4 80.75 323.0 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 3 401 135 861 34 50116 1 25.65 25.65 vendas_part1_20260206_022707.csv 2026-02-06T05:27:29.399Z 7 452 16

---
---

<br><br><br><br><br>